# Web API: cnyes & 104.com

- [slide](https://docs.google.com/presentation/d/1gn4d5gzXzgyEAIz_AOdM3pmJ0-6iiN7EbTjKqCQlgPo/edit?usp=sharing) for getting json data online
- Finding data url
- Scraping 104.com job info
- Understanding how to send request and get back response
- Send request with Cookie, payload, Referer...


## Send web requests

* Document: http://docs.python-requests.org/en/master/ 
* Quickstart http://docs.python-requests.org/en/master/user/quickstart/

瀏覽器在瀏覽一個頁面時，實際上所做的動作是對對對方伺服器發出一個HTTP要求（request），對方伺服器會根據這個要求合不合法來決定要給對方什麼樣的回應（response）。這些回應主要有如[HTTP Status Code](https://en.wikipedia.org/wiki/List_of_HTTP_status_codes)上所有的情形。例如對方伺服器如果發現要求的內容是對的，但權限是有問題的，就會回應一個「403 Forbidden」的狀態碼（Status Code）。而如果能夠順利拿回資料的話，便會回應「200 OK」並把所要求的資料在回應中傳回來。

HTTP要求有兩類，分別是`GET()`和`POST()`。`POST()`通常是要填寫表單資訊的時候所送出的要求，例如需要指明要哪一區、哪一種類型的房子、或哪一種類型的車票等。而一般新聞網站或社群網站多會用`GET()`取回資料。

In [2]:
import requests
import json
response = requests.get('https://tcgbusfs.blob.core.windows.net/dotapp/youbike/v2/youbike_immediate.json')
response.json()
type(response.json())

list

### Practice: Find out and traverse data behind urls

逐一測試過每一個link是否都讀得到資料，以獲得對這些資料概略了解。
* (hint) Using `requests.get(url, timeout=(x, y))` to set the limitation of waiting time
* `timeout=(x, y)`: Max x seconds to connect to server and max y seconds to wait on response
* https://data.moi.gov.tw/moiod/System/Principle.aspx?Sample=2

#### Canyes

In [3]:
url_cnyes = "https://news.cnyes.com/api/v3/news/category/headline?startAt=1588262400&endAt=1589212799&limit=30"
res = requests.get(url_cnyes).json()
print(type(res))
print(res.keys())

<class 'dict'>
dict_keys(['items', 'message', 'statusCode'])


#### PChome 24h product search

In [4]:
url_pchome = "https://ecshweb.pchome.com.tw/search/v3.3/all/results?q=iphone&page=1&sort=sale/dc"
res = requests.get(url_pchome).json()
print(type(res))
print(res.keys())

<class 'dict'>
dict_keys(['QTime', 'totalRows', 'totalPage', 'range', 'cateName', 'q', 'subq', 'token', 'isMust', 'prods'])


#### Dcard

Dcard API最近又做了改版，用以下的Code應該沒辦法順利撈回，但你也可以測試看看，可以看到什麼樣的錯誤訊息。

In [5]:
url_dcard = "https://www.dcard.tw/service/api/v2/forums/relationship/posts?limit=50"
user_agent_dcard = "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/106.0.0.0 Safari/537.36 Edg/106.0.1370.34"
headers = {'User-Agent': user_agent_dcard}
res = requests.get(url_dcard, headers = headers)
print(res)

<Response [403]>


### (Option) Write a function to load json data

In [6]:
def get_web_json(url, headers=""):
    response = requests.get(url, timeout=(3, 5), headers=headers)
    print("Response Code:", response.status_code)
    if not response.ok:
        return None
    data = response.json()
    return data

# get_web_json(url_pchome)
# get_web_json(url_cnyes)

## Scraping 104.com
* Slide: https://docs.google.com/presentation/d/e/2PACX-1vRW84XoB5sFRT1Eg-GrK4smX23qoNkFffz_h8oRU4AIvJAgrrxBn8059_0UeHv_pFBks_Z37vNbLGai/pub?start=false&loop=false&delayms=3000


Address

```
https://www.104.com.tw/jobs/search/list?ro=0&kwop=7&keyword=data%20scientist&expansionType=area%2Cspec%2Ccom%2Cjob%2Cwf%2Cwktm&order=14&asc=0&page=2&mode=s&jobsource=2018indexpoc
```

### Step01. Get the 1st page (but fails)

先嘗試用上面的方法獲取104.com的搜尋結果的第一頁資料網址，結果應該會傳回來一個空的HTML無法傳回資料。這是因為通常服務提供方會嘗試要求提出拜訪要求的瀏覽器需要提供一些簡單的驗證機制，例如是用什麼瀏覽器連上去的（稱為User-agent，DCard會要求這樣的資訊）、是從哪一個頁面跳過去的（稱為Referer，104.com就有這樣的要求）。

撰寫爬蟲時必須「模仿」瀏覽器的機制，如果對方希望瀏覽器提供這樣的資訊，那撰寫爬蟲時也就要提供這樣的資訊。


In [14]:
url_104 = 'https://www.104.com.tw/jobs/search/api/jobs?jobsource=index_s&keyword=%E8%B3%87%E6%96%99%E7%A7%91%E5%AD%B8&mode=s&order=15&page=1&pagesize=20&'
response = requests.get(url_104)
print(response.status_code)

403


In [15]:
print(response.text)

<html><head></head><body></body></html>


In [16]:
print(response.headers)

{'Date': 'Thu, 27 Mar 2025 07:03:44 GMT', 'Content-Type': 'text/html; charset=utf-8', 'Transfer-Encoding': 'chunked', 'Connection': 'keep-alive', 'Vary': 'Accept-Encoding', 'cf-cache-status': 'DYNAMIC', 'Server': 'cloudflare', 'CF-RAY': '926d078d3f2d8463-TPE', 'Content-Encoding': 'gzip'}


#### Trick. Write html to file

當明明知道他是一個json，卻一直無法順利用`.json()`將其拆且為`list` or `dict`的型態時，最有可能的問題是，該網址設了一些檢核機制讓我們不能那麼粗暴草率地拿到資料，導致它傳回來給我們的是一個用html編寫成的錯誤訊息，例如stuatus code: 403。這時候我要怎麼知道發生錯誤？一種方式是把status code印出來看看；另一種方式是，他可能也是傳給你status code:200，但實際上就是傳回一個告知你不能存取的html。這時候我們可以採取的作法就是把該HTML，也就是回傳的結果寫入到.html檔，然後用瀏覽器開啟看看他究竟傳回來什麼錯誤訊息。

觀察上面`response.text`中的回應顯然是以HTML格式撰寫，而下方程式碼會把回應內容寫到一個HTML檔案裡面去，可以在本機端或CoLab上點開該HTML檔來觀察看看究竟傳回來什麼東西。

In [17]:
with open('temp_output.html', 'w') as fout:
    fout.write(response.text)

# webbrowser cannot work, why?
import webbrowser
webbrowser.open_new_tab('temp_output.html')

True

#### Practice. Observe youbike data headers

Youtube data所回傳的是一個JSON檔，而上述104.com目前回傳的資料內容是個HTML檔，觀察看看，youbike回應標題是什麼（response headers）？如果要很會寫爬蟲，一定要會觀察header，而這只是最簡單的一種情形。


In [10]:
import requests
import json
response = requests.get('https://tcgbusfs.blob.core.windows.net/dotapp/youbike/v2/youbike_immediate.json')

print(response)
print(response.status_code)
print(type(response)) # <class 'requests.models.Response'>
print(type(response.text)) # <class 'str'>

<Response [200]>
200
<class 'requests.models.Response'>
<class 'str'>


In [11]:
print(response.headers)
import pandas as pd
print(pd.DataFrame.from_dict(response.headers, orient='index'))

{'Content-Length': '808175', 'Content-Type': 'application/json; charset=UTF-8', 'Content-MD5': 'GUUFXOo9Y2wD0Chb/C2WNA==', 'Last-Modified': 'Thu, 27 Mar 2025 06:59:08 GMT', 'ETag': '0x8DD6CFCDF3ECF66', 'Server': 'Windows-Azure-Blob/1.0 Microsoft-HTTPAPI/2.0', 'x-ms-request-id': '477ebc9f-701e-0040-4de5-9e6791000000', 'x-ms-version': '2009-09-19', 'x-ms-lease-status': 'unlocked', 'x-ms-blob-type': 'BlockBlob', 'Access-Control-Allow-Origin': '*', 'Date': 'Thu, 27 Mar 2025 07:00:05 GMT'}
                                                                        0
Content-Length                                                     808175
Content-Type                              application/json; charset=UTF-8
Content-MD5                                      GUUFXOo9Y2wD0Chb/C2WNA==
Last-Modified                               Thu, 27 Mar 2025 06:59:08 GMT
ETag                                                    0x8DD6CFCDF3ECF66
Server                       Windows-Azure-Blob/1.0 Microsoft-HTTP

### Step02. Add Referer to get 104 data

現在我們來加入一些對方伺服器可能會要求我們發出request的時候提供的東西，最常見的有以下的資訊。但，實際上我們得一個一個測試看看，才會知道對方要求什麼。通常會從User-agent測起，再來Referer、再來Cookie。但有經驗的人多半一看就猜得到。

* User-Agent: 你用什麼瀏覽器或系統
* Referer: 你從哪個頁面點選、跳轉過來
* Cookies: 經過與伺服器建立連結後，他給了你什麼資訊好讓你持續可以待在這個頁面。

下方程式碼在送出`GET()`要求時也一併送出了Referer的資訊`'https://www.104.com.tw/'`，意義相當於偽裝成先打開104.com的首頁後，從首頁進入這個查詢連結。理論上如果沒進入首頁，就直接進入查詢連結，不是非常可疑嗎？所以，有些伺服器會偵測，這個要求是從哪一個頁面網址點選後轉過來的，

In [30]:
url_104 = 'https://www.104.com.tw/jobs/search/api/jobs?jobsource=index_s&keyword=%E8%B3%87%E6%96%99%E7%A7%91%E5%AD%B8&mode=s&order=15&page=1&pagesize=20'
headers = {
    'referer': 'https://www.104.com.tw/',
    'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/106.0.0.0 Safari/537.36 Edg/106.0.1370.34'
}

raw = requests.get(url_104, headers=headers).json()
type(raw)

dict

### Step03. Traverse data to get the data block

觀察一下資料的概況，並把他轉為pandas來觀察它。

In [28]:
print(raw.keys())
print(type(raw['data']))
print(type(raw['data'][0]))
df = pd.DataFrame(raw['data'])
df
# print(raw['data'].keys())
# print(type(raw['data']['list']))
# print(type(raw['data']['list'][0]))
# df = pd.DataFrame(raw['data']['list'])
# df

dict_keys(['data', 'metadata'])
<class 'list'>
<class 'dict'>


appearDate  applyCnt  coIndustry coIndustryDesc           custName  \
0    20250324         5  1004001007          金融控股業       富邦產物保險股份有限公司   
1    20250325         1  1013001002           國防事業          國家中山科學研究院   
2    20250319         7  1001004001           光電產業         聯齊科技股份有限公司   
3    20250327         8  1004003001          人身保險業  (總公司)南山人壽保險股份有限公司   
4    20250313        12  1001001002        電腦軟體服務業         詠鋐智能股份有限公司   
5    20250304         9  1001001002        電腦軟體服務業         維曙智能科技有限公司   
6    20250325         8  1006003001        廣告行銷公關業         浩騰媒體股份有限公司   
7    20250324         9  1001001003        網際網路相關業        易可思科技股份有限公司   
8    20250304        11  1001001002        電腦軟體服務業         維曙智能科技有限公司   
9    20250325        11  1006002002            電視業        緯來電視網股份有限公司   
10   20250325         7  1004001007          金融控股業  國泰金控_國泰金融控股股份有限公司   
11   20250324        12  1001001006     其它軟體及網路相關業         皓博科技股份有限公司   
12   20250327         7  1008003006    其他專業／科學及技術業   工研院 _財團法人工業技術研究院   
13   20250324         3  1001001002        電腦軟體服務業         緯謙科技股份有限公司   
14   20250326         8  1001001006     其它軟體及網路相關業         圖策科技股份有限公司   
15   20250326         7  1001001002        電腦軟體服務業   QNAP_威聯通科技股份有限公司   
16   20250324         9  1008003006    其他專業／科學及技術業   工研院 _財團法人工業技術研究院   
17   20250320        18  1008003001        工商顧問服務業         創代科技股份有限公司   
18   20250324         5  1001006002         半導體製造業       中國砂輪企業股份有限公司   
19   20250325         8  1004001007          金融控股業  國泰金控_國泰金融控股股份有限公司   
20   20250325        13  1004001001            銀行業     國泰世華商業銀行股份有限公司   
21   20250324         6  1003001015      綜合商品批發代理業       華翰物產實業股份有限公司   

             custNo                                        description  \
0       70826461000  ★富邦產險招募MA：經營管理組\n目標以成為企業及個人保險之全方位經營管理人才為發展方向，歷...   
1   130000000055232  錄取後依考生學經歷、專長、個人特質賦予以下部分或多項工作：\n1. 各類契約（包含中、英文契...   
2   130000000047967  【關於 NextDrive 資料團隊】\nNextDrive 資料團隊專注於資料洞察與應用，...   
3       11456006000  推動人工智能 (AI) 和其他資料科學新技術的應用，並將其成功地導入企業流程中，以提高效率、...   
4   130000000186926  執行資料科學專案，包含理解商務問題、資料分析、提出並驗證解決方案，以及展示專案成果。  \n...   
5   130000000229061  會是您大展身手的地方。歡迎加入我們。\n\n作為資料科學家，需要對新技術保有高度熱誠，能夠歸...   
6       16832894000  道，協助生成動態數據可視化報告 ，讓內部團隊和客戶能快速理解數據結果並做出策略性決策。\n4...   
7   130000000215354  \n2. 機器學習與深度學習演算法開發及優化。\n3. 進行資料統計分析與視覺化。\n4. ...   
8   130000000229061  會是您大展身手的地方。歡迎加入我們。\n\n作為資料科學家，需要對新技術保有高度熱誠，能夠歸...   
9       20913187000  1. 進行數據清洗、資料貼標以及特徵工程等資料前處理工作。 \n2. 選用資料科學或人工智慧...   
10      70827406000  [工作內容]\n職務包含但不限於以下內容\n- 基於 Python 語言之產品開發，推廣及後...   
11  130000000076068  與部署。\n\n資料科學家在現今數據化時代中扮演重要的角色，憑藉數據分析技能和洞察力，能夠協...   
12       2750963000  1. 資料分析軟體模組開發、系統整合與測試。 \n2. 針對資料科學應用主題瞭解領域知識，並...   
13  130000000175101  透過數據蒐集、資料分析與可視化架構，解決商業痛點推動業務增長並提升運營效率，與各部門緊密協作...   
14  130000000151165  【職位名稱】 金融資料科學工程師\n\n【工作內容】\n1. 負責金融數據的蒐集、前處理與清...   
15      80682695000  [工作內容]\n1. 透過 NLP 相關技術優化 Chatbot，以提升客戶體驗。\n2. ...   
16       2750963000  \n\n【研究室簡介】\n本研究室專注在發展應用於材料科學與產業之AI相關技術，透過AI平台...   
17  130000000123231  我們正在尋找具備 LLM 經驗的資料科學家 Data Scientist，主要負責 大型語言...   
18       3089008000  1. 維護已開發之AI模型與Web介面\n2. 協助整合外部合作學校/公司開發之AI模型與W...   
19      70827406000  【團隊介紹】\n我們是一個充滿熱情與創意的團隊，致力於結合科技與數據驅動保險業的創新變革。在...   
20       4231910004  性的環境下，實現個人專業成長、累積市場能見度，一起跟上東南亞數位金融市場的快速成長!\n\n...   
21      80378420000  ●我們正在尋找數名資料科學家，此職位將\n1. 與領域專家結合資料面將商業問題轉化為可分析的...   

                                          descSnippet  mrtDist  \
0   ★富邦產險招募MA：經營管理組\n目標以成為企業及個人保險之全方位經營管理人才為發展方向，歷...     0.00   
1   錄取後依考生學經歷、專長、個人特質賦予以下部分或多項工作：\n1. 各類契約（包含中、英文契...     0.00   
2   【關於 NextDrive [[[資料]]]團隊】\nNextDrive [[[資料]]]團...     0.32   
3   推動人工智能 (AI) 和其他[[[資料科學]]]新技術的應用，並將其成功地導入企業流程中，...     0.21   
4   執行[[[資料科學]]]專案，包含理解商務問題、[[[資料]]]分析、提出並驗證解決方案，以...     0.06   
5   會是您大展身手的地方。歡迎加入我們。\n\n作為[[[資料科學]]]家，需要對新技術保有高度...     0.18   
6   道，協助生成動態數據可視化報告 ，讓內部團隊和客戶能快速理解數據結果並做出策略性決策。\n4...     0.03   
7   \n2. 機器學習與深度學習演算法開發及優化。\n3. 進行[[[資料]]]統計分析與視覺化...     0.32   
8   會是您大展身手的地方。歡迎加入我們。\n\n

### Step04. Get next page: get the 2nd, 1st, 3rd, ..., page urls

接下來要從Chrome Development Tools來觀察，下二頁、三頁、四頁的網址為何（例如以下網址）。然後要去觀察這些網址的變化，應該不難觀察在page=1, page=2, page=3的數字上有所變化。通常這種網址的變化都是有規律性的。
```
https://www.104.com.tw/jobs/search/api/jobs?jobsource=index_s&keyword=%E8%B3%87%E6%96%99%E7%A7%91%E5%AD%B8&mode=s&order=15&page=2&pagesize=20


https://www.104.com.tw/jobs/search/api/jobs?jobsource=index_s&keyword=%E8%B3%87%E6%96%99%E7%A7%91%E5%AD%B8&mode=s&order=15&page=3&pagesize=20


https://www.104.com.tw/jobs/search/api/jobs?jobsource=index_s&keyword=%E8%B3%87%E6%96%99%E7%A7%91%E5%AD%B8&mode=s&order=15&page=40&pagesize=20
```

因為知道有這樣的規律性，所以就拆解要發出的網址，把網址的頁碼的獨立出來，然後用for-loop來走過每個頁面。

In [32]:



for page in range(1, 6):
    url = 'https://www.104.com.tw/jobs/search/api/jobs?jobsource=index_s&keyword=%E8%B3%87%E6%96%99%E7%A7%91%E5%AD%B8&mode=s&order=15&page=' + str(page) + '&pagesize=20'
    # url = 'https://www.104.com.tw/jobs/search/list?ro=0&kwop=7&keyword=data%20scientist&expansionType=area%2Cspec%2Ccom%2Cjob%2Cwf%2Cwktm&order=14&asc=0&page=' + str(page) + '&mode=s&jobsource=2018indexpoc'
    raw = requests.get(url, headers=headers).json()
    print(len(raw['data']))

22
22
22
22
22


除了列印出來以外，用`all_data`這個變項儲存資料，並在for-loop中把每一頁的資料用`extend()`附加到`all_data`中。

以下程式碼要注意的是，因為頁面沒有第0頁，但`range()`預設是從0開始，所以此時要特別寫定`range()`要從1開始。

In [ ]:
all_data = []
for page in range(1, 3):
    url = 'https://www.104.com.tw/jobs/search/api/jobs?jobsource=index_s&keyword=%E8%B3%87%E6%96%99%E7%A7%91%E5%AD%B8&mode=s&order=15&page=' + str(page) + '&pagesize=20'
    raw = requests.get(url, headers=headers).json()
    all_data.extend(raw['data'])
    print(len(all_data))

22
44
66
88
110


最後我們把整筆資料轉為pandas比較好觀察。

In [34]:
df = pd.DataFrame(all_data)
print(df.shape)
print(len(set(df.jobNo)))

(110, 41)
110


### Step05. Detect ending condition

前面的步驟中我們知道要如何一步一步抓取每一頁的資料，最後還有一個問題就是，抓到什麼時候才要停？通常程式設計師也得留一個線索，才知道要如何在網頁上自動化呈現最後一頁（如同你看網頁時所看到的最後一頁的頁碼）。所以我們得去揣測程式設計師的邏輯，看他是怎麼設計最後一頁的停止機制的。

通常最主要有兩種：
1. 直接顯示最後一頁是多少：那就寫一個爬蟲，直接去偵測這個最後一頁是多少，然後把他當成ending condition。如104.com的例子是有總資料筆數的，除以頁數就可以知道總頁數。
2. 不直接顯示最後一頁是多少（e.g. PCHOME），就設一個夠大的迴圈，讓爬蟲抓抓抓抓到當掉，或者抓到資料沒再新增了，我們就偵測如果抓到的資料是零筆，就讓他跳出迴圈。

In [40]:
print(raw.keys())
print(type(raw['data']))
print(raw['metadata'].keys())
print(raw['metadata']['pagination'])
print(raw['metadata']['pagination']['lastPage'])

# print(raw['data']['pageNo'])
# print("Total Page:", raw['data']['totalPage'])
# print(raw['data']['count'])
# print(raw['data']['totalCount'])

dict_keys(['data', 'metadata'])
<class 'list'>
dict_keys(['pagination', 'isPreciseHotJob', 'filterQuery', 'personalBoost'])
{'count': 22, 'currentPage': 5, 'lastPage': 94, 'total': 1867}
94


#### Trick. pprint (pretty-print)
https://docs.python.org/3/library/pprint.html. ... The pprint module provides a capability to “pretty-print” arbitrary Python data structures in a form which can be used as input to the interpreter ...

Example
```python
class pprint.PrettyPrinter(indent=1, width=80, depth=None, stream=None, *, compact=False, sort_dicts=True, underscore_numbers=False)¶
```

In [42]:
import pprint
pp = pprint.PrettyPrinter(indent=4)
pp.pprint(raw['data'][:2])

[   {   'appearDate': '20250327',
        'applyCnt': 4,
        'applyDate': None,
        'coIndustry': 1002001010,
        'coIndustryDesc': '其他食品製造業',
        'custName': '百鮮企業有限公司',
        'custNo': '22857149000',
        'd3': '08:00-17:00',
        'descSnippet': '百鮮位於新北市林口（靠近醒吾科技大學），主要經營食品調味料、辛香料、機能飲品調味，通過ISO22000及FSSC認證，屬於北部稍具規模的食品加工廠；公司團隊年輕有活力，並有很大的發展空間，歡迎所有有心在食品也發展的夥伴加入我們的行列！！\n'
                       '\n'
                       '【工作內容】\n'
                       '\n'
                       '    #廠區巡檢及生產管理衛生稽核\n'
                       '    #週期性產品檢驗\n'
                       '    #程序書維護與更新\n'
                       '    #進行法規資訊蒐集，並建立資料庫\n'
                       '    #生產文件管理與稽核應對\n'
                       '    #熟悉ISO22000及HACCP，協助規劃食品安全衛生教育訓練計劃\n'
                       '    #協助產品專案研究計畫之規劃與執行',
        'description': '百鮮位於新北市林口（靠近醒吾科技大學），主要經營食品調味料、辛香料、機能飲品調味，通過ISO22000及FSSC認證，屬於北部稍具規模的食品加工廠；公司團隊年輕有活力，並有很大的發展空間，歡迎所有有心在食品也發展的夥伴加入我們的行列！！\n'
                       '\n'
        

In [45]:
totalPage = raw['metadata']['pagination']['lastPage']


all_data = []

# Uncomment the next line code to scrape from 1 to totalage
totalPage = 2
for page in range(1, totalPage+1):
    url = 'https://www.104.com.tw/jobs/search/api/jobs?jobsource=index_s&keyword=%E8%B3%87%E6%96%99%E7%A7%91%E5%AD%B8&mode=s&order=15&page=' + str(page) + '&pagesize=20'
    raw = requests.get(url, headers=headers).json()
    all_data.extend(raw['data'])
    print(len(all_data))


22
44


### 6. convert to dataframe

In [46]:
df = pd.DataFrame(all_data)
print(df.shape)
df

(44, 41)


appearDate  applyCnt  coIndustry coIndustryDesc  \
0    20250324         5  1004001007          金融控股業   
1    20250325         1  1013001002           國防事業   
2    20250319         7  1001004001           光電產業   
3    20250327         8  1004003001          人身保險業   
4    20250313        12  1001001002        電腦軟體服務業   
5    20250304         9  1001001002        電腦軟體服務業   
6    20250325         8  1006003001        廣告行銷公關業   
7    20250324         9  1001001003        網際網路相關業   
8    20250304        11  1001001002        電腦軟體服務業   
9    20250325        11  1006002002            電視業   
10   20250325         7  1004001007          金融控股業   
11   20250324        12  1001001006     其它軟體及網路相關業   
12   20250327         7  1008003006    其他專業／科學及技術業   
13   20250324         3  1001001002        電腦軟體服務業   
14   20250326         8  1001001006     其它軟體及網路相關業   
15   20250326         7  1001001002        電腦軟體服務業   
16   20250324         9  1008003006    其他專業／科學及技術業   
17   20250320        18  1008003001        工商顧問服務業   
18   20250324         5  1001006002         半導體製造業   
19   20250325         8  1004001007          金融控股業   
20   20250325        13  1004001001            銀行業   
21   20250324         6  1003001015      綜合商品批發代理業   
22   20250327         2  1011002002       建物裝修及裝潢業   
23   20250325         5  1011002002       建物裝修及裝潢業   
24   20250224         1  1005001007       大專校院教育事業   
25   20250311         9  1001003003     消費性電子產品製造業   
26   20250327        10  1002015001      精密儀器相關製造業   
27   20250327         6  1001004001           光電產業   
28   20250325         2  1004001001            銀行業   
29   20250115        18  1004001001            銀行業   
30   20250324        14  1001003001    電腦及其週邊設備製造業   
31   20241217        14  1001001003        網際網路相關業   
32   20250324         9  1004003001          人身保險業   
33   20250322        14  1001001002        電腦軟體服務業   
34   20250324         8  1001004002        光學器材製造業   
35   20240808         9  1001006001        IC設計相關業   
36   20250123        19  1001006001        IC設計相關業   
37   20250326         2  1001001005         數位內容產業   
38   20250320         2  1004001001            銀行業   
39   20250327        14  1003001004  家庭電器／設備及用品批發業   
40   20250323        17  1001001003        網際網路相關業   
41   20250321        14  1001002001          電信相關業   
42   20250319        11  1008003001        工商顧問服務業   
43   20250325        17  1004001001            銀行業   

                              custName           custNo  \
0                         富邦產物保險股份有限公司      70826461000   
1                            國家中山科學研究院  130000000055232   
2                           聯齊科技股份有限公司  130000000047967   
3                    (總公司)南山人壽保險股份有限公司      11456006000   
4                           詠鋐智能股份有限公司  130000000186926   
5                           維曙智能科技有限公司  130000000229061   
6                           浩騰媒體股份有限公司      16832894000   
7                          易可思科技股份有限公司  130000000215354   
8                           維曙智能科技有限公司  130000000229061   
9                          緯來電視網股份有限公司      20913187000   
10                   國泰金控_國泰金融控股股份有限公司      70827406000   
11                          皓博科技股份有限公司  130000000076068   
12                    工研院 _財團法人工業技術研究院       2750963000   
13                          緯謙科技股份有限公司  130000000175101   
14                          圖策科技股份有限公司  130000000151165   
15                    QNAP_威聯通科技股份有限公司      80682695000   
16                    工研院 _財團法人工業技術研究院       2750963000   
17                          創代科技股份有限公司  130000000123231   
18                        中國砂輪企業股份有限公司       3089008000   
19                   國泰金控_國泰金融控股股份有限公司      70827406000   
20                      國泰世華商業銀行股份有限公司       4231910004   
21                        華翰物產實業股份有限公司      80378420000   
22             名匠博物館多媒體設計_名匠設計室內裝修有限公司      15879744000   
23             名匠博物館多媒體設計_名匠設計室內裝修有限公司      15879744000   
24                        慈濟學校財團法人慈濟大學       8152423000   
25                         優式機器人股份有限公司

## Dump files for backup

* 因為抓取資料很久很辛苦，所以通常會把它寫到後端的檔案、資料庫，或者雲端的資料庫中。在此，我們選擇把他寫到pandas或者`.json()`比較好讀的json檔。通常不會寫到CSV，因為CSV是以逗點分隔為辨識基礎，但文本中可能也會有逗點，會比較容易出錯。
* 建議若設計了寫入，就立刻讀出來看看，省得不小心寫入錯誤，屆時程式關閉了，資料就取不回來了。
* 還有另外一種檔案是python的pickle檔。pickle是一種暫存檔，也就是我們現在如果有一個變數是pandas dataframe，寫到pickle再讀出來，他還會是一個pandas dataframe，而且資料型態都不會變。這點其實非常好用，因為如果你把一個dataframe轉為json，你要特別注意那些datetime欄位或multiindex的東西被轉成什麼，又是否能夠讀得回來。也就是如果時間物件要寫入到json檔時，理應要先轉成string，然後讀取回來要做分析時，也要再轉回來datetime。但如果你轉為pickle檔，存進去是什麼樣子，拿出來就是什麼樣子。那pickle檔有缺點嗎？有！就和其他的程式例如R或網頁程式無法通用，也無法直接寫到雲端資料庫。


### M1. Dump one variable to json by json library
* https://docs.python.org/3/library/json.html

In [90]:
import json

# Uncomment the following code
# with open('104_list.json', 'w') as outfile:
#     json.dump(all_data, outfile)

### M2. Dump and load json by pandas library

In [78]:
# Uncomment the following code

# with open('104_df.json', 'w') as f:
#     f.write(df.to_json())

In [84]:
# Uncomment the following code
# Read-back

# pd.read_json("104_df.json")

jobType     jobNo                                            jobName  \
0           1  12901787                                     日班倉管員(週休二日免排班)   
1           1  11726918                            水晶軒專櫃店長(台中區)底薪固定13個月+獎金   
2           1   8422468  (Human Resources) Learning and Development Tea...   
3           1  12388507  [2022科技菁英計畫]  產品測試工程師 Product/Test Engineer [限...   
4           1  12781781  【外商】財務分析副理 Finance Planning &amp; Analysis Ass...   
...       ...       ...                                                ...   
1425        2  13009437                                    Data Specialist   
1426        0  12850348     微生物(資深) 研究員_Microbiology Senior(Sr.) Scientist   
1427        2  12823438                                資料工程師 Data Engineer   
1428        0  13029724                                Data Engineer 數據工程師   
1429        0  12096096                                              資料科學家   

                                         jobNameSnippet  jobRole  jobRo  \
0                                        日班倉管員(週休二日免排班)        1      1   
1                               水晶軒專櫃店長(台中區)底薪固定13個月+獎金        1      1   
2     (Human Resources) Learning and Development Tea...        1      1   
3     [2022科技菁英計畫]  產品測試工程師 Product/Test Engineer [限...        1      1   
4     【外商】財務分析副理 Finance Planning &amp; Analysis Ass...        1      1   
...                                                 ...      ...    ...   
1425  <em class='b-txt--highlight'>Data</em> Specialist        1      1   
1426  微生物(資深) 研究員_Microbiology Senior(Sr.) <em class...        1      1   
1427  資料工程師 <em class='b-txt--highlight'>Data</em> E...        1      1   
1428  <em class='b-txt--highlight'>Data</em> Enginee...        1      1   
1429            <em class='b-txt--highlight'>資料科學家</em>        1      1   

       jobAddrNo jobAddrNoDesc  jobAddress  \
0     6001005012        桃園市大園區               
1     6001008004         台中市西區               
2     6001002011        新北市新店區               
3     6001002015        新北市中和區   興南路一段142號   
4     6001001004        台北市松山區  敦化北路88號13樓   
...          ...           ...         ...   
1425  6001001003        台北市中山區  南京東路三段168號   
1426  6001002025        新北市五股區     五工六路25號   
1427  6001001005        台北市大安區    近忠孝復興捷運站   
1428  6001016015        高雄市路竹區               
1429  6001001001        台北市中正區  羅斯福路一段七號六樓   

                                            description  ...             tags  \
0     1.倉儲貨品管理及貨品環境維護 \n2.物流倉儲各項改包進貨及出貨作業,熟悉倉庫生態佳 \n...  ...   [外商公司, 員工650人]   
1     百貨公司專櫃儲備幹部及店長職務\r\n1.負責介紹及銷售商品。 \r\n2.提供顧客之接待與...  ...   [外商公司, 員工190人]   
2     About HTC\n\nHTC built a vision of the future ...  ...  [上市上櫃, 員工2000人]   
3     ▋ 關於德州儀器\n德州儀器(TI)是位居類比晶片世界領導地位的半導體設計與製造公司，持續提...  ...  [外商公司, 員工2000人]   
4     Planning and Budgeting\n- Assist in the prepar...  ...   [外商公司, 員工250人]   
...                                                 ...  ...              ...   
1425  The [[[Data]]] Specialist is responsible for l...  ...   [外商公司, 員工100人]   
1426  Position Summary:\nPharmacology Discovery Serv...  ...         [員工130人]   
1427   與PM/UI/UX、前後端、資料、演算法工程師一同合作，開發與維護產品。\n   2. 負...  ...         [員工650人]   
1428   do we manage the complexities of our manufact...  ...         [員工260人]   
1429  1.建構數據分析環境。\n2.以機器、深度學習與統計分析等最佳化研究與開發。\n3.規劃數據...  ...          [員工80人]   

            landmark                                               link  \
0                     {'applyAnalyze': '//www.104.com.tw/jobs/apply/...   
1                     {'applyAnalyze': '//www.104.com.tw/jobs/apply/...   
2                     {'applyAnalyze': '//www.104.com.tw/jobs/apply/...   
3       距捷運南勢角站320公尺  {'applyAnalyze': '//www.104.com.tw/jobs/apply/...   
4     距捷運台北小巨蛋站340公尺  {'applyAnalyze': '//www.104.com.tw/jobs/apply/...   
...              ...                                                ...   
1425   距捷運南京復興站230公尺  {'applyAnalyze': '//www.104.com.tw/jobs/apply/...   
1426                  {'applyAnalyze': '//

### M3. Dump multiple variables to pickle

```python
import pickle
with open('104.pkl', 'wb') as fout:  # Python 3: open(..., 'wb')
    pickle.dump([all_data, df], fout)
```

In [26]:
# Uncomment the following code

import pickle
# with open('104.pkl', 'wb') as fout:  # Python 3: open(..., 'wb')
#     pickle.dump([all_data, df], fout)

#### Load multiple variables back to objects

```python
with open('104.pkl', "rb") as fin:  # Python 3: open(..., 'rb')
    test = pickle.load(fin)
    print(type(test[0]))
    print(type(test[1]))
```

In [91]:
# Uncomment the following code

# with open('104.pkl', "rb") as fin:  # Python 3: open(..., 'rb')
#     test = pickle.load(fin)
#     print(type(test[0]))
#     print(type(test[1]))

In [92]:
# Uncommment the following code

# test[0][0].keys()

## Using timestamp as file name

因為我們抓取資料的for-loop如果有幾千或幾萬個iterations，勢必很怕抓到一半斷掉或當機，卻又得重抓。所以最好的方式就是，每抓個幾百筆或幾千筆，就留一份檔案。但要如何區分這些檔案的先後順序？通常會用撈取的時間加上資料筆數的先後來作為檔名的一部分，這樣之後就可以觀看這些檔名來知道，究竟資料有沒有抓完，或者當在哪裡。

下面的程式碼將取得的現在時間加到檔名中

```python
with open('104_%s.pkl'%(now), 'wb') as fout:  # Python 3: open(..., 'wb')
    pickle.dump([all_data, df], fout)
```

In [29]:
from datetime import datetime

now = datetime.now().strftime("%Y%m%d%H%M%S")
print("Current Time =", now)

# with open('104_%s.pkl'%(now), 'wb') as fout:  # Python 3: open(..., 'wb')
#     pickle.dump([all_data, df], fout)

Current Time = 20221010120556
